# Unweighted Average

In [1]:
# Importing the libraries
import numpy as np
import pandas as pd
import sklearn
import matplotlib.pyplot as plt
import sys
import numpy
numpy.set_printoptions(threshold=sys.maxsize)

# Importing the dataset
dataset = pd.read_csv('CVD dataset2.csv')
data=dataset.iloc[:, :].values
X = dataset.iloc[:, :-1].values
y = dataset.iloc[:, 16].values
# X = dataset.iloc[:, [ 0, 1, 2, 5, 10, 11, 13, 15]].values

rows = len(data)    # 3 rows in your example
cols = len(data[0])
print(rows)
print(cols)

560
17


In [2]:
dataNoCvd = data[~(data[:,16] > 0.0)]
dataCvd = data[~(data[:,16] < 1.0)]
rowsNoCvd = len(dataNoCvd)    
rowsCvd = len(dataCvd)
print(rowsNoCvd)
print(rowsCvd)
# print(dataNoCvd)
# print(dataCvd)

519
41


In [3]:
def find_NoCvd_limitsArray(i,DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue):
    if i>0 :
        DownNoCvd = UpNoCvd
        UpNoCvd= fold_NoCvd_total+UpNoCvd
    if i < fold_NoCvd_residue :
        UpNoCvd+= 1
#     print("NoCvd limits, Down :",DownNoCvd,"Up ",UpNoCvd)
    return   DownNoCvd, UpNoCvd   
 
def find_Cvd_limitsArray(i,DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv):
    if i>0 :
        DownCvd = UpCvd
        UpCvd= fold_Cvd_total+UpCvd
    if i >= cv - fold_Cvd_residue :
         UpCvd+= 1     
#     print("Cvd limits, Down :",DownCvd,"Up ",UpCvd)
    return   DownCvd, UpCvd  

def find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1=dataNoCvd[DownNoCvd:UpNoCvd,:]
    temp2=dataCvd[DownCvd:UpCvd,:]
    temp3=np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

def find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1 = np.delete(dataNoCvd, slice(DownNoCvd, UpNoCvd), axis=0)
    temp2 = np.delete(dataCvd, slice(DownCvd, UpCvd), axis=0)
    temp3 = np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

In [4]:
def create_train_test_sets(cv,dataNoCvd,dataCvd):
    test_total = []
    train_total = []
    train_total_Cvd = []
    train_total_NoCvd = []
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)

    fold_Cvd_total = rowsCvd//cv
    fold_Cvd_residue= rowsCvd%cv
    print("fold_Cvd_total  :",fold_Cvd_total," fold_Cvd_residue  :",fold_Cvd_residue)

    fold_NoCvd_total = rowsNoCvd//cv
    fold_NoCvd_residue= rowsNoCvd%cv
    print("fold_NoCvd_total:",fold_NoCvd_total,"fold_NoCvd_residue:",fold_NoCvd_residue)

    DownNoCvd=0
    DownCvd=0
    UpNoCvd = fold_NoCvd_total
    UpCvd = fold_Cvd_total

    for i in range(cv):
        X_test = []
        y_test = []
        X_train = []
        y_train = []
#         print("============",i,"==============")
        DownNoCvd, UpNoCvd = find_NoCvd_limitsArray(i, DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue)
        DownCvd, UpCvd = find_Cvd_limitsArray(i, DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv)

        testSubset_NoCvd ,testSubset_Cvd ,testSubset_total = find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
        trainSubset_NoCvd ,trainSubset_Cvd ,trainSubset_total = find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
     
    #creating X_train, y_train, X_test, y_test
        X_test.append(np.delete(testSubset_total, 16, axis=1))
        y_test_temp = np.delete(testSubset_total, slice(0, 16), axis=1)
        y_test.append(np.reshape(y_test_temp, len(y_test_temp)))
        X_test_temp = np.array(X_test)
        X_test = X_test_temp[0]
        y_test_temp = np.array(y_test)
        y_test = y_test_temp[0]
    
        X_train.append(np.delete(trainSubset_total, 16, axis=1))
        y_train_temp = np.delete(trainSubset_total, slice(0, 16), axis=1)
        y_train.append(np.reshape(y_train_temp, len(y_train_temp)))
        X_train_temp = np.array(X_train)
        X_train = X_train_temp[0]
        y_train_temp = np.array(y_train)
        y_train = y_train_temp[0]
        
    #add every subset in a list so we can handle thm later 
        test_total.append([X_test,y_test])
        train_total.append([X_train,y_train]) 
        train_total_NoCvd.append(trainSubset_NoCvd)
        train_total_Cvd.append(trainSubset_Cvd)
    return train_total, test_total, train_total_NoCvd, train_total_Cvd

In [5]:
train_total, test_total, train_total_NoCvd, train_total_Cvd = create_train_test_sets(10,dataNoCvd,dataCvd)

fold_Cvd_total  : 4  fold_Cvd_residue  : 1
fold_NoCvd_total: 51 fold_NoCvd_residue: 9


In [6]:
# Chech ratio in each train and test set
def find_ratio(index_list):
    one = 0
    lenght=len(index_list[0])
    for i in range(lenght):
#         print(index_list[1])
        if index_list[1][i] == 1.0 :
            one+= 1
    ratio = one/lenght
    return ratio

for i in range(10):
    print(len(train_total[i][0]))
    ratio = find_ratio(train_total[i])
    print("ratio in train set:", ratio)
    ratio = find_ratio(test_total[i])
    print("ratio in test set:", ratio)

504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07142857142857142
ratio in test set: 0.08928571428571429


In [7]:
from xgboost import XGBClassifier


def my_fit(ratio,dataNoCvd,dataCvd,params):   
    Subarray=[]
    models = []
    # yarray
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)
#     print("Size of NoCvd cases in train set:",rowsNoCvd)
#     print("Size of Cvd cases in train set  :",rowsCvd)


    numOfSubsamples = rowsNoCvd//(rowsCvd*ratio)
    numOfSubsamples= int(numOfSubsamples)
    SubNoCvd = rowsNoCvd//numOfSubsamples
    residue = rowsNoCvd- SubNoCvd*numOfSubsamples


    Up = 0


    for i in range(numOfSubsamples):
        
        classifier = XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=params[5],
                  colsample_bynode=1, colsample_bytree=1, gamma=params[4],
                  learning_rate=params[0], max_delta_step=0, max_depth=params[1],
                  min_child_weight=params[3], missing=None, n_estimators=params[2], n_jobs=1,
                  nthread=None, objective='binary:logistic', random_state=0,
                  reg_alpha=0, reg_lambda=params[6], scale_pos_weight=params[7], seed=None,
                  silent=None, subsample=1.0, verbosity=1)
    #     print(i)
    #Creating the training set for each model
        Down = Up
        Up= Up + SubNoCvd
        if i < residue :
            Up+= 1
        
#         print(Down)
#         print(Up)
        
        Sub1=dataNoCvd[Down:Up,:]
        Sub2=np.concatenate((Sub1, dataCvd))
        Subarray.append(Sub2)
        
    #Dividing to X and y of the previous traing set    
        X=np.delete(Subarray[i], 16, axis=1)
        y=np.delete(Subarray[i], slice(0, 16), axis=1)
        y=np.reshape(y, len(y))
        
        classifier.fit( X, y)
        models.append(classifier)
    return models     

In [39]:
models = my_fit(2,dataNoCvd,dataCvd)   

TypeError: my_fit() missing 1 required positional argument: 'params'

In [8]:


def predict_unweighted_average(models,X):
    y_pred = []
    y_pred_models = []

    models_size = len(models)
    X_size = len(X)
       
    #βρίσκω και αποθηκευω τα predictions κάθε μοντέλου για το Χ_test όχι όμως με την μορφή (0,1) όπως θα έκανε η
# predict αλλά με μορφή πιθανότητας να έρθει 1 με την predict_proba, δηλαδή τώρα ο πίνακας y_pred_models έχει τις 
# πιθανότητες κάθε περίπτωση του X_test να εμφανίσει Cvd
    for i in range(models_size): 
        y_pred_models.append(models[i].predict_proba(X)[:,1]) 

#Παίρνω τις πιθανότητες κάθε μοντέλου και για κάθε μία περίπτωση του X_test κάνω το average των πιθανοτήτων αυτών
# οπότε βγαίνει μια μέση πιθανότητα για κάθε μία περίπτωση του X_test.
    for j in range(X_size):
        sum = 0
        for i in range(models_size):
            sum = sum + y_pred_models[i][j]
        avr = sum/models_size
        if avr>= 0.5 :         #Όμως επειδή θεωρώ ότι το μοντέλο κάνει classification αν η μέση πιθανότητα 
            y_pred.append(1.)  # είναι μεγαλυτερη από 0.5 τότε θα επιστρέφει 1, δηλαδή ότι έχει cvd, αλλιώς 0
        else:
            y_pred.append(0.)
    return y_pred        
  

In [24]:
y_pred = predict_unweighted_average(models,test_total[9][0])

In [25]:
print(y_pred)
# print(y_pred_models[0])

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 1.0]


In [9]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from sklearn import metrics

def my_cross_val( cv, train_total, test_total, train_total_NoCvd, train_total_Cvd,params):
    accuracy = []
    specificity = []
    sensitivity = []
    auc = []
    
    # print(X)
    for i in range(cv):
#         X_train = train_total[i][0]
#         y_train = train_total[i][1]
        X_test = test_total[i][0]
        y_test = test_total[i][1]
        


        models = my_fit( 1, train_total_NoCvd[i], train_total_Cvd[i],params)


        y_pred = predict_unweighted_average(models,X_test)

        cm = confusion_matrix(y_test, y_pred)
    #     print(cm)

        total1=sum(sum(cm))
        #####from confusion matrix calculate accuracy
        accuracy1=(cm[0,0]+cm[1,1])/total1
    #   print ('Accuracy : ', accuracy1)

        specificity1 = cm[0,0]/(cm[0,0]+cm[0,1])
    #   print('Specificity : ', specificity1 )

        sensitivity1 = cm[1,1]/(cm[1,0]+cm[1,1])
    #   print('Sensitivity : ', sensitivity1)
        
#         y = np.array(y_test)
#         pred = np.array(y_pred)
#         fpr, tpr, thresholds = metrics.roc_curve(y, pred, pos_label=2)
#         auc1 = metrics.auc(fpr, tpr)
        
        auc1 = roc_auc_score(y_test, y_pred)

    
        accuracy.append(accuracy1)
        specificity.append(specificity1)
        sensitivity.append(sensitivity1) 
        auc.append(auc1)
    return accuracy, specificity, sensitivity, auc

In [28]:
# https://www.analyticsvidhya.com/blog/2016/03/complete-guide-parameter-tuning-xgboost-with-codes-python/        
params = {
                    "learning_rate"    :[ 0.1, 0.2, 0.3],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300],
                     "subsample"       :[0.5,0.75, 1.0],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3]
        }
parameters : [0.5, 1, 100, 1, 0, 1.0, 1, 5]
accuracy : 0.6125
spes     : 0.6110105580693816
sens     : 0.64
auc      : 0.6255052790346908



In [23]:
params = {
                    "learning_rate"    :[ 0.5],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100],
                    "min_child_weight" :[1],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[1.0], #0.5-1
                     "reg_lambda"      :[1], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[5]
        }

In [24]:
comb = compute_comb(params)
print(comb[0])
accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,comb[0])

[0.5, 1, 100, 1, 0, 1.0, 1, 5]


In [25]:
from statistics import mean
print(mean(accuracy))
print(mean(specificity))
print(mean(sensitivity))
print(mean(auc))

0.6267857142857143
0.6262820512820513
0.64
0.6331410256410256


In [10]:
# https://www.geeksforgeeks.org/python-all-possible-permutations-of-n-lists/

def compute_comb(params):
    
    # initializing lists 
    list1 = params.get("learning_rate")
    list2 = params.get("max_depth")
    list3 = params.get("n_estimators") 
    list4 = params.get("min_child_weight")
    list5 = params.get("gamma")    
    list6 = params.get("colsample_bytree")
    list7 = params.get("reg_lambda") 
    list8 = params.get("scale_pos_weight")

#     # printing lists  
#     print ("The original lists are : " + str(list1) +
#                                    " " + str(list2) + 
#                                    " " + str(list3) + 
#                                    " " + str(list4) + 
#                                    " " + str(list5) + 
#                                    " " + str(list6) +
#                                    " " + str(list7) +
#                                    " " + str(list8)) 

    # using list comprehension  
    # to compute all possible permutations 
    res = [[i, j, k, l, m, n, o, p] for i in list1  
                                    for j in list2 
                                    for k in list3 
                                    for l in list4 
                                    for m in list5 
                                    for n in list6 
                                    for o in list7
                                    for p in list8] 

    # printing result 
#     print ("All possible permutations are : " +  str(res))
    return res

In [11]:
class style:
    BOLD = '\033[1m'
    END = '\033[0m'

In [12]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from statistics import mean

def gridsearch(params):
    max_sens = 0
    max_spes = 0
    max_acc = 0
    best_params = []
    max_params = []
    max_auc = 0
    combs = compute_comb(params)
    print(len(combs))
    for j in range(len(combs)):
        print(j)
        accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,combs[j])
        if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5:
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
            print(combs[j])
            print (style.BOLD + 'accuracy    ' + style.END, mean(accuracy))
            print (style.BOLD + 'specificity ' + style.END, mean(specificity))
            print (style.BOLD + 'sensitivity ' + style.END, mean(sensitivity))
            print (style.BOLD + 'auc         ' + style.END, mean(auc))
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
        else:
            print(combs[j])
            print("accuracy    ",mean(accuracy))
            print("specificity ",mean(specificity))
            print("sensitivity ",mean(sensitivity))
            print("auc         ",mean(auc))
        best_params.append([combs[j],mean(accuracy),mean(specificity),mean(sensitivity),mean(auc)])
        if mean(auc)> max_auc:
            max_sens = mean(sensitivity)
            max_spes = mean(specificity)
            max_acc = mean(accuracy)
            max_auc = mean(auc)
            max_params = combs[j]
    return max_sens, max_params, max_spes, max_acc, max_auc, best_params

# Ratio = 2

 Αποτέλεσμα της gridsearch με τις ακόλουθες παραμέτρους, γίνονται print όλα και αυτά που ικανοποιούν την συνθήκη : if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5 είναι με bold και μεταξύ γραμμών.

In [13]:
# https://www.analyticsvidhya.com/blog/2016/03/complete-guide-parameter-tuning-xgboost-with-codes-python/        
params = {
                    "learning_rate"    :[0.2, 0.3,0.4,0.5],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[2, 3,4,5,6],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400,500],
                    "min_child_weight" :[2],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[2,3,4,5]
        }

In [14]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

7200
0
[0.2, 2, 100, 2, 0, 0.5, 1, 2]
accuracy     0.7267857142857143
specificity  0.7534690799396682
sensitivity  0.39
auc          0.571734539969834
1
----------------------------------------------------------------
[0.2, 2, 100, 2, 0, 0.5, 1, 3]
accuracy     0.6625
specificity  0.6725867269984918
sensitivity  0.54
auc          0.6062933634992459
----------------------------------------------------------------
2
----------------------------------------------------------------
[0.2, 2, 100, 2, 0, 0.5, 1, 4]
accuracy     0.6446428571428571
specificity  0.6494720965309201
sensitivity  0.59
auc          0.61973604826546
----------------------------------------------------------------
3
----------------------------------------------------------------
[0.2, 2, 100, 2, 0, 0.5, 1, 5]
accuracy     0.6160714285714286
specificity  0.6187028657616893
sensitivity  0.59
auc          0.6043514328808446
----------------------------------------------------------------
4
[0.2, 2, 100, 2, 0, 0.5, 1.5, 

----------------------------------------------------------------
[0.2, 2, 100, 2, 0, 1.0, 1.5, 5]
accuracy     0.6107142857142858
specificity  0.61289592760181
sensitivity  0.59
auc          0.6014479638009049
----------------------------------------------------------------
32
[0.2, 2, 100, 2, 0, 1.0, 2, 2]
accuracy     0.7035714285714285
specificity  0.7283559577677224
sensitivity  0.39
auc          0.5591779788838612
33
----------------------------------------------------------------
[0.2, 2, 100, 2, 0, 1.0, 2, 3]
accuracy     0.6732142857142858
specificity  0.6841251885369533
sensitivity  0.54
auc          0.6120625942684766
----------------------------------------------------------------
34
----------------------------------------------------------------
[0.2, 2, 100, 2, 0, 1.0, 2, 4]
accuracy     0.6214285714285714
specificity  0.6244343891402715
sensitivity  0.59
auc          0.6072171945701357
----------------------------------------------------------------
35
[0.2, 2, 100, 2, 0

----------------------------------------------------------------
[0.2, 2, 100, 2, 0.5, 1.0, 1, 5]
accuracy     0.6303571428571428
specificity  0.6282805429864253
sensitivity  0.665
auc          0.6466402714932127
----------------------------------------------------------------
64
[0.2, 2, 100, 2, 0.5, 1.0, 1.5, 2]
accuracy     0.7178571428571429
specificity  0.743815987933635
sensitivity  0.39
auc          0.5669079939668175
65
----------------------------------------------------------------
[0.2, 2, 100, 2, 0.5, 1.0, 1.5, 3]
accuracy     0.675
specificity  0.6840874811463047
sensitivity  0.565
auc          0.6245437405731523
----------------------------------------------------------------
66
----------------------------------------------------------------
[0.2, 2, 100, 2, 0.5, 1.0, 1.5, 4]
accuracy     0.6375
specificity  0.6398567119155354
sensitivity  0.615
auc          0.6274283559577677
----------------------------------------------------------------
67
---------------------------

[0.2, 2, 200, 2, 0, 1.0, 1, 4]
accuracy     0.6785714285714286
specificity  0.6957013574660633
sensitivity  0.465
auc          0.5803506787330317
99
----------------------------------------------------------------
[0.2, 2, 200, 2, 0, 1.0, 1, 5]
accuracy     0.6678571428571428
specificity  0.6783559577677225
sensitivity  0.54
auc          0.6091779788838613
----------------------------------------------------------------
100
[0.2, 2, 200, 2, 0, 1.0, 1.5, 2]
accuracy     0.7267857142857143
specificity  0.7534313725490196
sensitivity  0.39
auc          0.5717156862745097
101
[0.2, 2, 200, 2, 0, 1.0, 1.5, 3]
accuracy     0.7035714285714285
specificity  0.7265082956259427
sensitivity  0.415
auc          0.5707541478129713
102
----------------------------------------------------------------
[0.2, 2, 200, 2, 0, 1.0, 1.5, 4]
accuracy     0.6857142857142857
specificity  0.6995852187028657
sensitivity  0.515
auc          0.6072926093514329
--------------------------------------------------------

----------------------------------------------------------------
[0.2, 2, 200, 2, 0.5, 0.75, 2, 3]
accuracy     0.6767857142857143
specificity  0.6860859728506787
sensitivity  0.565
auc          0.6255429864253393
----------------------------------------------------------------
130
----------------------------------------------------------------
[0.2, 2, 200, 2, 0.5, 0.75, 2, 4]
accuracy     0.6375
specificity  0.6417797888386124
sensitivity  0.59
auc          0.6158898944193062
----------------------------------------------------------------
131
----------------------------------------------------------------
[0.2, 2, 200, 2, 0.5, 0.75, 2, 5]
accuracy     0.625
specificity  0.6245098039215686
sensitivity  0.64
auc          0.6322549019607843
----------------------------------------------------------------
132
[0.2, 2, 200, 2, 0.5, 1.0, 1, 2]
accuracy     0.7321428571428571
specificity  0.7553544494720965
sensitivity  0.44
auc          0.5976772247360482
133
---------------------------

...

[0.5, 6, 200, 2, 0.5, 0.75, 2, 4]
accuracy     0.6803571428571429
specificity  0.6995852187028657
sensitivity  0.44
auc          0.5697926093514328
6971
[0.5, 6, 200, 2, 0.5, 0.75, 2, 5]
accuracy     0.6696428571428571
specificity  0.6861236802413273
sensitivity  0.465
auc          0.5755618401206637
6972
[0.5, 6, 200, 2, 0.5, 1.0, 1, 2]
accuracy     0.7178571428571429
specificity  0.7496229260935143
sensitivity  0.32
auc          0.5348114630467571
6973
[0.5, 6, 200, 2, 0.5, 1.0, 1, 3]
accuracy     0.6928571428571428
specificity  0.7130844645550528
sensitivity  0.44
auc          0.5765422322775264
6974
[0.5, 6, 200, 2, 0.5, 1.0, 1, 4]
accuracy     0.6839285714285714
specificity  0.7034313725490197
sensitivity  0.44
auc          0.5717156862745097
6975
[0.5, 6, 200, 2, 0.5, 1.0, 1, 5]
accuracy     0.6535714285714286
specificity  0.670814479638009
sensitivity  0.44
auc          0.5554072398190045
6976
[0.5, 6, 200, 2, 0.5, 1.0, 1.5, 2]
accuracy     0.7285714285714285
specificity  0.7554

[0.5, 6, 300, 2, 0.5, 0.5, 1.5, 2]
accuracy     0.7285714285714286
specificity  0.7651206636500754
sensitivity  0.27
auc          0.5175603318250377
7025
[0.5, 6, 300, 2, 0.5, 0.5, 1.5, 3]
accuracy     0.7035714285714285
specificity  0.7304298642533937
sensitivity  0.365
auc          0.5477149321266969
7026
[0.5, 6, 300, 2, 0.5, 0.5, 1.5, 4]
accuracy     0.6785714285714286
specificity  0.6995852187028657
sensitivity  0.415
auc          0.5572926093514329
7027
[0.5, 6, 300, 2, 0.5, 0.5, 1.5, 5]
accuracy     0.6482142857142857
specificity  0.6668552036199095
sensitivity  0.415
auc          0.5409276018099547
7028
[0.5, 6, 300, 2, 0.5, 0.5, 2, 2]
accuracy     0.7357142857142858
specificity  0.7708521870286577
sensitivity  0.29
auc          0.5304260935143288
7029
[0.5, 6, 300, 2, 0.5, 0.5, 2, 3]
accuracy     0.6928571428571428
specificity  0.7130467571644042
sensitivity  0.44
auc          0.5765233785822022
7030
[0.5, 6, 300, 2, 0.5, 0.5, 2, 4]
accuracy     0.6892857142857143
specificity 

[0.5, 6, 400, 2, 0, 0.75, 2, 3]
accuracy     0.725
specificity  0.7496229260935143
sensitivity  0.415
auc          0.5823114630467572
7078
[0.5, 6, 400, 2, 0, 0.75, 2, 4]
accuracy     0.7035714285714285
specificity  0.7245475113122172
sensitivity  0.44
auc          0.5822737556561086
7079
[0.5, 6, 400, 2, 0, 0.75, 2, 5]
accuracy     0.6892857142857143
specificity  0.7130467571644042
sensitivity  0.39
auc          0.5515233785822021
7080
[0.5, 6, 400, 2, 0, 1.0, 1, 2]
accuracy     0.7303571428571428
specificity  0.7708521870286577
sensitivity  0.215
auc          0.4929260935143288
7081
[0.5, 6, 400, 2, 0, 1.0, 1, 3]
accuracy     0.7392857142857143
specificity  0.7630467571644042
sensitivity  0.44
auc          0.6015233785822022
7082
[0.5, 6, 400, 2, 0, 1.0, 1, 4]
accuracy     0.7089285714285715
specificity  0.7265082956259427
sensitivity  0.49
auc          0.6082541478129714
7083
[0.5, 6, 400, 2, 0, 1.0, 1, 5]
accuracy     0.6910714285714286
specificity  0.7073529411764705
sensitivity  

[0.5, 6, 500, 2, 0, 0.5, 1, 4]
accuracy     0.7089285714285715
specificity  0.7361613876319759
sensitivity  0.365
auc          0.550580693815988
7131
[0.5, 6, 500, 2, 0, 0.5, 1, 5]
accuracy     0.7071428571428572
specificity  0.7265460030165912
sensitivity  0.465
auc          0.5957730015082956
7132
[0.5, 6, 500, 2, 0, 0.5, 1.5, 2]
accuracy     0.7517857142857143
specificity  0.786236802413273
sensitivity  0.315
auc          0.5506184012066365
7133
[0.5, 6, 500, 2, 0, 0.5, 1.5, 3]
accuracy     0.7375
specificity  0.7611990950226244
sensitivity  0.44
auc          0.6005995475113122
7134
[0.5, 6, 500, 2, 0, 0.5, 1.5, 4]
accuracy     0.7017857142857142
specificity  0.7245475113122172
sensitivity  0.415
auc          0.5697737556561085
7135
[0.5, 6, 500, 2, 0, 0.5, 1.5, 5]
accuracy     0.6892857142857143
specificity  0.7111613876319759
sensitivity  0.415
auc          0.5630806938159879
7136
[0.5, 6, 500, 2, 0, 0.5, 2, 2]
accuracy     0.7232142857142857
specificity  0.7592006033182503
sensit

[0.5, 6, 500, 2, 0.5, 0.75, 2, 2]
accuracy     0.7339285714285715
specificity  0.7592006033182503
sensitivity  0.415
auc          0.5871003016591252
7185
[0.5, 6, 500, 2, 0.5, 0.75, 2, 3]
accuracy     0.7
specificity  0.7168929110105581
sensitivity  0.49
auc          0.603446455505279
7186
[0.5, 6, 500, 2, 0.5, 0.75, 2, 4]
accuracy     0.6857142857142857
specificity  0.7053544494720966
sensitivity  0.44
auc          0.5726772247360482
7187
[0.5, 6, 500, 2, 0.5, 0.75, 2, 5]
accuracy     0.6660714285714285
specificity  0.6822775263951735
sensitivity  0.465
auc          0.5736387631975867
7188
[0.5, 6, 500, 2, 0.5, 1.0, 1, 2]
accuracy     0.7178571428571429
specificity  0.7496229260935143
sensitivity  0.32
auc          0.5348114630467571
7189
[0.5, 6, 500, 2, 0.5, 1.0, 1, 3]
accuracy     0.6928571428571428
specificity  0.7130844645550528
sensitivity  0.44
auc          0.5765422322775264
7190
[0.5, 6, 500, 2, 0.5, 1.0, 1, 4]
accuracy     0.6839285714285714
specificity  0.7034313725490197
s

In [15]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.5, 2, 100, 2, 0.5, 0.75, 1, 5]
0.6678571428571428
0.6706636500754148
0.64
0.6553318250377074


In [17]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.65 :
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.2, 2, 400, 2, 0.5, 0.5, 1.5, 5]
accuracy : 0.6607142857142857
spes     : 0.6629713423831071
sens     : 0.64
auc      : 0.6514856711915535
------------------------------------------------
parameters : [0.2, 2, 500, 2, 0.5, 0.5, 1.5, 5]
accuracy : 0.6607142857142857
spes     : 0.6629713423831071
sens     : 0.64
auc      : 0.6514856711915535
------------------------------------------------
parameters : [0.4, 2, 400, 2, 0.5, 0.75, 1, 4]
accuracy : 0.6875
spes     : 0.6937782805429864
sens     : 0.615
auc      : 0.6543891402714932
------------------------------------------------
parameters : [0.5, 2, 100, 2, 0.5, 0.75, 1, 5]
accuracy : 0.6678571428571428
spes     : 0.6706636500754148
sens     : 0.64
auc      : 0.6553318250377074
------------------------------------------------
parameters : [0.5, 2, 200, 2, 0.5, 0.75, 1, 5]
accuracy : 0.6625
spes     : 0.664894419306184
sens     : 0.64
auc      : 0.652447209653092
------------------------------------------------
parameters : 

## Καλύτερες τιμές για Ratio = 2 με min_child_weight=2:

    parameters : [0.5, 2, 100, 2, 0.5, 0.75, 1, 5]
    accuracy : 0.6678571428571428
    spes     : 0.6706636500754148
    sens     : 0.64
    auc      : 0.6553318250377074

# Ratio = 3

Αποτέλεσμα της gridsearch με τις ακόλουθες παραμέτρους, γίνονται print όλα και αυτά που ικανοποιούν την συνθήκη : if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5 είναι με bold και μεταξύ γραμμών.

In [16]:
params = {
                    "learning_rate"    :[0.1,0.2, 0.3,0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400],
                    "min_child_weight" :[2],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3,4]
        }


In [17]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

6912
0
[0.1, 1, 100, 2, 0, 0.5, 1, 1]
accuracy     0.9053571428571429
specificity  0.9711538461538461
sensitivity  0.07
auc          0.520576923076923
1
[0.1, 1, 100, 2, 0, 0.5, 1, 2]
accuracy     0.7821428571428571
specificity  0.8209276018099547
sensitivity  0.29
auc          0.5554638009049774
2
----------------------------------------------------------------
[0.1, 1, 100, 2, 0, 0.5, 1, 3]
accuracy     0.6410714285714285
specificity  0.6515082956259427
sensitivity  0.515
auc          0.5832541478129714
----------------------------------------------------------------
3
[0.1, 1, 100, 2, 0, 0.5, 1, 4]
accuracy     0.5107142857142857
specificity  0.4971719457013575
sensitivity  0.685
auc          0.5910859728506788
4
[0.1, 1, 100, 2, 0, 0.5, 1.5, 1]
accuracy     0.9089285714285714
specificity  0.975
sensitivity  0.07
auc          0.5225
5
[0.1, 1, 100, 2, 0, 0.5, 1.5, 2]
accuracy     0.7803571428571429
specificity  0.8209276018099547
sensitivity  0.265
auc          0.5429638009049773
6


[0.1, 1, 100, 2, 0.5, 0.5, 2, 2]
accuracy     0.7839285714285714
specificity  0.8248114630467571
sensitivity  0.265
auc          0.5449057315233786
46
[0.1, 1, 100, 2, 0.5, 0.5, 2, 3]
accuracy     0.6410714285714286
specificity  0.6533559577677225
sensitivity  0.49
auc          0.5716779788838612
47
[0.1, 1, 100, 2, 0.5, 0.5, 2, 4]
accuracy     0.5125
specificity  0.5010558069381599
sensitivity  0.66
auc          0.5805279034690799
48
[0.1, 1, 100, 2, 0.5, 0.75, 1, 1]
accuracy     0.9071428571428571
specificity  0.9730769230769231
sensitivity  0.07
auc          0.5215384615384615
49
[0.1, 1, 100, 2, 0.5, 0.75, 1, 2]
accuracy     0.7803571428571429
specificity  0.8209653092006033
sensitivity  0.265
auc          0.5429826546003016
50
----------------------------------------------------------------
[0.1, 1, 100, 2, 0.5, 0.75, 1, 3]
accuracy     0.6375
specificity  0.6476244343891403
sensitivity  0.515
auc          0.5813122171945702
--------------------------------------------------------

[0.1, 1, 100, 2, 1, 0.75, 1.5, 4]
accuracy     0.5089285714285714
specificity  0.49524886877828056
sensitivity  0.685
auc          0.5901244343891403
92
[0.1, 1, 100, 2, 1, 0.75, 2, 1]
accuracy     0.9125
specificity  0.9788461538461538
sensitivity  0.07
auc          0.5244230769230769
93
[0.1, 1, 100, 2, 1, 0.75, 2, 2]
accuracy     0.7875
specificity  0.8286953242835596
sensitivity  0.265
auc          0.5468476621417798
94
----------------------------------------------------------------
[0.1, 1, 100, 2, 1, 0.75, 2, 3]
accuracy     0.6410714285714286
specificity  0.6514705882352941
sensitivity  0.515
auc          0.5832352941176471
----------------------------------------------------------------
95
[0.1, 1, 100, 2, 1, 0.75, 2, 4]
accuracy     0.5142857142857143
specificity  0.5029411764705882
sensitivity  0.66
auc          0.5814705882352941
96
[0.1, 1, 100, 2, 1, 1.0, 1, 1]
accuracy     0.9089285714285714
specificity  0.975
sensitivity  0.07
auc          0.5225
97
[0.1, 1, 100, 2, 1, 

[0.1, 1, 200, 2, 0, 1.0, 1, 4]
accuracy     0.5821428571428572
specificity  0.5801282051282052
sensitivity  0.615
auc          0.5975641025641025
136
[0.1, 1, 200, 2, 0, 1.0, 1.5, 1]
accuracy     0.8839285714285714
specificity  0.9480392156862745
sensitivity  0.07
auc          0.5090196078431373
137
[0.1, 1, 200, 2, 0, 1.0, 1.5, 2]
accuracy     0.7571428571428571
specificity  0.7900829562594268
sensitivity  0.34
auc          0.5650414781297134
138
----------------------------------------------------------------
[0.1, 1, 200, 2, 0, 1.0, 1.5, 3]
accuracy     0.6660714285714286
specificity  0.6744343891402715
sensitivity  0.565
auc          0.6197171945701357
----------------------------------------------------------------
139
[0.1, 1, 200, 2, 0, 1.0, 1.5, 4]
accuracy     0.5767857142857143
specificity  0.5743589743589743
sensitivity  0.615
auc          0.5946794871794872
140
[0.1, 1, 200, 2, 0, 1.0, 2, 1]
accuracy     0.8857142857142857
specificity  0.9499622926093514
sensitivity  0.07
a

----------------------------------------------------------------
[0.1, 1, 200, 2, 0.5, 1.0, 2, 3]
accuracy     0.6642857142857143
specificity  0.6725113122171946
sensitivity  0.565
auc          0.6187556561085973
----------------------------------------------------------------
179
[0.1, 1, 200, 2, 0.5, 1.0, 2, 4]
accuracy     0.5714285714285714
specificity  0.5685897435897436
sensitivity  0.615
auc          0.5917948717948718
180
[0.1, 1, 200, 2, 1, 0.5, 1, 1]
accuracy     0.9071428571428571
specificity  0.9730769230769231
sensitivity  0.07
auc          0.5215384615384615
181
[0.1, 1, 200, 2, 1, 0.5, 1, 2]
accuracy     0.7571428571428571
specificity  0.7900829562594268
sensitivity  0.34
auc          0.5650414781297134
182
----------------------------------------------------------------
[0.1, 1, 200, 2, 1, 0.5, 1, 3]
accuracy     0.6732142857142858
specificity  0.6821266968325792
sensitivity  0.565
auc          0.6235633484162896
---------------------------------------------------------

...

[0.4, 4, 200, 2, 0.5, 1.0, 1.5, 4]
accuracy     0.7982142857142858
specificity  0.8343891402714932
sensitivity  0.34
auc          0.5871945701357466
6656
[0.4, 4, 200, 2, 0.5, 1.0, 2, 1]
accuracy     0.8535714285714285
specificity  0.9095022624434389
sensitivity  0.145
auc          0.5272511312217194
6657
[0.4, 4, 200, 2, 0.5, 1.0, 2, 2]
accuracy     0.8321428571428571
specificity  0.8806184012066365
sensitivity  0.22
auc          0.5503092006033182
6658
[0.4, 4, 200, 2, 0.5, 1.0, 2, 3]
accuracy     0.8089285714285714
specificity  0.8555429864253393
sensitivity  0.22
auc          0.5377714932126697
6659
[0.4, 4, 200, 2, 0.5, 1.0, 2, 4]
accuracy     0.7839285714285714
specificity  0.8248114630467571
sensitivity  0.265
auc          0.5449057315233785
6660
[0.4, 4, 200, 2, 1, 0.5, 1, 1]
accuracy     0.8732142857142857
specificity  0.9326168929110106
sensitivity  0.12
auc          0.5263084464555052
6661
[0.4, 4, 200, 2, 1, 0.5, 1, 2]
accuracy     0.8357142857142857
specificity  0.88446455

[0.4, 4, 300, 2, 0, 0.75, 1, 3]
accuracy     0.8089285714285714
specificity  0.8574660633484162
sensitivity  0.195
auc          0.5262330316742081
6711
[0.4, 4, 300, 2, 0, 0.75, 1, 4]
accuracy     0.7982142857142857
specificity  0.8497737556561086
sensitivity  0.145
auc          0.49738687782805424
6712
[0.4, 4, 300, 2, 0, 0.75, 1.5, 1]
accuracy     0.8446428571428571
specificity  0.9017722473604827
sensitivity  0.12
auc          0.5108861236802413
6713
[0.4, 4, 300, 2, 0, 0.75, 1.5, 2]
accuracy     0.8267857142857142
specificity  0.8825414781297134
sensitivity  0.12
auc          0.5012707390648568
6714
[0.4, 4, 300, 2, 0, 0.75, 1.5, 3]
accuracy     0.8142857142857143
specificity  0.8651960784313726
sensitivity  0.165
auc          0.5150980392156863
6715
[0.4, 4, 300, 2, 0, 0.75, 1.5, 4]
accuracy     0.8053571428571429
specificity  0.8516968325791855
sensitivity  0.215
auc          0.5333484162895927
6716
[0.4, 4, 300, 2, 0, 0.75, 2, 1]
accuracy     0.8410714285714286
specificity  0.89

[0.4, 4, 300, 2, 0.5, 1.0, 2, 2]
accuracy     0.8321428571428571
specificity  0.8806184012066365
sensitivity  0.22
auc          0.5503092006033182
6766
[0.4, 4, 300, 2, 0.5, 1.0, 2, 3]
accuracy     0.8089285714285714
specificity  0.8555429864253393
sensitivity  0.22
auc          0.5377714932126697
6767
[0.4, 4, 300, 2, 0.5, 1.0, 2, 4]
accuracy     0.7839285714285714
specificity  0.8248114630467571
sensitivity  0.265
auc          0.5449057315233785
6768
[0.4, 4, 300, 2, 1, 0.5, 1, 1]
accuracy     0.8732142857142857
specificity  0.9326168929110106
sensitivity  0.12
auc          0.5263084464555052
6769
[0.4, 4, 300, 2, 1, 0.5, 1, 2]
accuracy     0.8357142857142857
specificity  0.8844645550527903
sensitivity  0.22
auc          0.5522322775263951
6770
[0.4, 4, 300, 2, 1, 0.5, 1, 3]
accuracy     0.8196428571428571
specificity  0.8613499245852188
sensitivity  0.29
auc          0.5756749622926094
6771
[0.4, 4, 300, 2, 1, 0.5, 1, 4]
accuracy     0.7892857142857143
specificity  0.830580693815987

[0.4, 4, 400, 2, 0, 0.75, 1.5, 1]
accuracy     0.8428571428571429
specificity  0.8998491704374058
sensitivity  0.12
auc          0.5099245852187029
6821
[0.4, 4, 400, 2, 0, 0.75, 1.5, 2]
accuracy     0.8339285714285715
specificity  0.8902714932126696
sensitivity  0.12
auc          0.5051357466063349
6822
[0.4, 4, 400, 2, 0, 0.75, 1.5, 3]
accuracy     0.8142857142857143
specificity  0.8671191553544495
sensitivity  0.14
auc          0.5035595776772247
6823
[0.4, 4, 400, 2, 0, 0.75, 1.5, 4]
accuracy     0.8017857142857143
specificity  0.8497737556561086
sensitivity  0.19
auc          0.5198868778280543
6824
[0.4, 4, 400, 2, 0, 0.75, 2, 1]
accuracy     0.8446428571428571
specificity  0.9017722473604827
sensitivity  0.12
auc          0.5108861236802413
6825
[0.4, 4, 400, 2, 0, 0.75, 2, 2]
accuracy     0.8267857142857142
specificity  0.8825414781297134
sensitivity  0.12
auc          0.5012707390648568
6826
[0.4, 4, 400, 2, 0, 0.75, 2, 3]
accuracy     0.8107142857142857
specificity  0.8593891

[0.4, 4, 400, 2, 0.5, 1.0, 2, 4]
accuracy     0.7839285714285714
specificity  0.8248114630467571
sensitivity  0.265
auc          0.5449057315233785
6876
[0.4, 4, 400, 2, 1, 0.5, 1, 1]
accuracy     0.8714285714285714
specificity  0.9306938159879337
sensitivity  0.12
auc          0.5253469079939668
6877
[0.4, 4, 400, 2, 1, 0.5, 1, 2]
accuracy     0.8321428571428571
specificity  0.8806184012066365
sensitivity  0.22
auc          0.5503092006033182
6878
[0.4, 4, 400, 2, 1, 0.5, 1, 3]
accuracy     0.8232142857142857
specificity  0.8632730015082957
sensitivity  0.315
auc          0.5891365007541478
6879
[0.4, 4, 400, 2, 1, 0.5, 1, 4]
accuracy     0.7892857142857143
specificity  0.8305806938159879
sensitivity  0.27
auc          0.5502903469079939
6880
[0.4, 4, 400, 2, 1, 0.5, 1.5, 1]
accuracy     0.8642857142857143
specificity  0.9248491704374058
sensitivity  0.095
auc          0.5099245852187029
6881
[0.4, 4, 400, 2, 1, 0.5, 1.5, 2]
accuracy     0.8392857142857143
specificity  0.8863876319758

In [19]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.2, 1, 300, 2, 0, 1.0, 1.5, 4]
0.6571428571428571
0.660972850678733
0.615
0.6379864253393664


In [21]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.63:
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.1, 2, 200, 2, 0.5, 1.0, 1, 4]
accuracy : 0.7517857142857143
spes     : 0.7727752639517346
sens     : 0.49
auc      : 0.6313876319758672
------------------------------------------------
parameters : [0.2, 1, 200, 2, 1, 1.0, 1, 3]
accuracy : 0.6714285714285715
spes     : 0.6782805429864254
sens     : 0.59
auc      : 0.6341402714932126
------------------------------------------------
parameters : [0.2, 1, 300, 2, 0, 0.5, 1.5, 4]
accuracy : 0.6535714285714286
spes     : 0.6571266968325792
sens     : 0.615
auc      : 0.6360633484162895
------------------------------------------------
parameters : [0.2, 1, 300, 2, 0, 0.5, 2, 4]
accuracy : 0.6517857142857143
spes     : 0.6552036199095023
sens     : 0.615
auc      : 0.6351018099547511
------------------------------------------------
parameters : [0.2, 1, 300, 2, 0, 0.75, 1.5, 4]
accuracy : 0.65
spes     : 0.6532805429864253
sens     : 0.615
auc      : 0.6341402714932126
------------------------------------------------
parameter

In [23]:
#Τυπώνονται περιπτώσεις που accuracy<0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][1] > 0.6 and best_params[i][2] > 0.6 and best_params[i][3] > 0.6 and best_params[i][4] > 0.62:
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.1, 1, 400, 2, 0, 0.5, 1, 4]
accuracy : 0.625
spes     : 0.6263574660633484
sens     : 0.615
auc      : 0.6206787330316742
------------------------------------------------
parameters : [0.1, 1, 400, 2, 0, 0.5, 1.5, 4]
accuracy : 0.625
spes     : 0.6263574660633484
sens     : 0.615
auc      : 0.6206787330316742
------------------------------------------------
parameters : [0.1, 1, 400, 2, 0, 0.5, 2, 4]
accuracy : 0.6285714285714286
spes     : 0.6302036199095022
sens     : 0.615
auc      : 0.6226018099547511
------------------------------------------------
parameters : [0.1, 1, 400, 2, 0, 0.75, 1.5, 4]
accuracy : 0.625
spes     : 0.6263574660633484
sens     : 0.615
auc      : 0.6206787330316742
------------------------------------------------
parameters : [0.1, 1, 400, 2, 0, 0.75, 2, 4]
accuracy : 0.625
spes     : 0.6263574660633484
sens     : 0.615
auc      : 0.6206787330316742
------------------------------------------------
parameters : [0.1, 1, 400, 2, 0, 1.0, 1.5, 4]


## Καλύτερες τιμές για Ratio = 3 με min_child_weight=2:

    parameters : [0.2, 1, 300, 2, 0, 1.0, 1.5, 4]
    accuracy : 0.6571428571428571
    spes     : 0.660972850678733
    sens     : 0.615
    auc      : 0.6379864253393664

    parameters : [0.2, 1, 300, 2, 1, 1.0, 1, 3]
    accuracy : 0.6714285714285715
    spes     : 0.6782805429864254
    sens     : 0.59
    auc      : 0.6341402714932126
    

# Ratio = 1

Αποτέλεσμα της gridsearch με τις ακόλουθες παραμέτρους, γίνονται print όλα και αυτά που ικανοποιούν την συνθήκη : if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5 είναι με bold και μεταξύ γραμμών.

In [13]:
params = {
                    "learning_rate"    :[0.1,0.2, 0.3,0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400],
                    "min_child_weight" :[2],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3,4]
        }

In [14]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

6912
0
[0.1, 1, 100, 2, 0, 0.5, 1, 1]
accuracy     0.5232142857142857
specificity  0.5222096530920061
sensitivity  0.54
auc          0.531104826546003
1
[0.1, 1, 100, 2, 0, 0.5, 1, 2]
accuracy     0.24107142857142858
specificity  0.18895173453996983
sensitivity  0.905
auc          0.5469758672699849
2
[0.1, 1, 100, 2, 0, 0.5, 1, 3]
accuracy     0.1517857142857143
specificity  0.08868778280542987
sensitivity  0.955
auc          0.5218438914027149
3
[0.1, 1, 100, 2, 0, 0.5, 1, 4]
accuracy     0.12857142857142856
specificity  0.06368778280542986
sensitivity  0.955
auc          0.509343891402715
4
[0.1, 1, 100, 2, 0, 0.5, 1.5, 1]
accuracy     0.5303571428571429
specificity  0.5260558069381599
sensitivity  0.59
auc          0.5580279034690799
5
[0.1, 1, 100, 2, 0, 0.5, 1.5, 2]
accuracy     0.22857142857142856
specificity  0.17545248868778282
sensitivity  0.905
auc          0.5402262443438914
6
[0.1, 1, 100, 2, 0, 0.5, 1.5, 3]
accuracy     0.1517857142857143
specificity  0.08868778280542987


[0.1, 1, 100, 2, 0.5, 0.75, 2, 1]
accuracy     0.5303571428571429
specificity  0.5260935143288085
sensitivity  0.59
auc          0.5580467571644042
57
[0.1, 1, 100, 2, 0.5, 0.75, 2, 2]
accuracy     0.21785714285714286
specificity  0.1638763197586727
sensitivity  0.905
auc          0.5344381598793364
58
[0.1, 1, 100, 2, 0.5, 0.75, 2, 3]
accuracy     0.14285714285714285
specificity  0.07907239819004525
sensitivity  0.955
auc          0.5170361990950226
59
[0.1, 1, 100, 2, 0.5, 0.75, 2, 4]
accuracy     0.11071428571428571
specificity  0.04441930618401207
sensitivity  0.955
auc          0.499709653092006
60
[0.1, 1, 100, 2, 0.5, 1.0, 1, 1]
accuracy     0.525
specificity  0.5222473604826546
sensitivity  0.565
auc          0.5436236802413272
61
[0.1, 1, 100, 2, 0.5, 1.0, 1, 2]
accuracy     0.23928571428571427
specificity  0.18699095022624435
sensitivity  0.905
auc          0.5459954751131222
62
[0.1, 1, 100, 2, 0.5, 1.0, 1, 3]
accuracy     0.15
specificity  0.08676470588235294
sensitivity  0

[0.1, 1, 200, 2, 0, 0.5, 1.5, 1]
accuracy     0.5285714285714286
specificity  0.5204374057315234
sensitivity  0.64
auc          0.5802187028657617
113
[0.1, 1, 200, 2, 0, 0.5, 1.5, 2]
accuracy     0.2857142857142857
specificity  0.24091251885369533
sensitivity  0.855
auc          0.5479562594268477
114
[0.1, 1, 200, 2, 0, 0.5, 1.5, 3]
accuracy     0.20892857142857144
specificity  0.15422322775263952
sensitivity  0.905
auc          0.5296116138763197
115
[0.1, 1, 200, 2, 0, 0.5, 1.5, 4]
accuracy     0.18214285714285713
specificity  0.12337858220211162
sensitivity  0.93
auc          0.5266892911010558
116
[0.1, 1, 200, 2, 0, 0.5, 2, 1]
accuracy     0.5285714285714286
specificity  0.5204374057315234
sensitivity  0.64
auc          0.5802187028657617
117
[0.1, 1, 200, 2, 0, 0.5, 2, 2]
accuracy     0.2839285714285714
specificity  0.2389894419306184
sensitivity  0.855
auc          0.5469947209653092
118
[0.1, 1, 200, 2, 0, 0.5, 2, 3]
accuracy     0.2017857142857143
specificity  0.146530920060

[0.1, 1, 200, 2, 0.5, 0.75, 2, 4]
accuracy     0.1732142857142857
specificity  0.11376319758672701
sensitivity  0.93
auc          0.5218815987933635
168
[0.1, 1, 200, 2, 0.5, 1.0, 1, 1]
accuracy     0.5303571428571429
specificity  0.5223227752639518
sensitivity  0.64
auc          0.5811613876319759
169
[0.1, 1, 200, 2, 0.5, 1.0, 1, 2]
accuracy     0.29464285714285715
specificity  0.2505656108597285
sensitivity  0.855
auc          0.5527828054298642
170
[0.1, 1, 200, 2, 0.5, 1.0, 1, 3]
accuracy     0.2125
specificity  0.15806938159879336
sensitivity  0.905
auc          0.5315346907993967
171
[0.1, 1, 200, 2, 0.5, 1.0, 1, 4]
accuracy     0.18928571428571428
specificity  0.13110859728506788
sensitivity  0.93
auc          0.530554298642534
172
[0.1, 1, 200, 2, 0.5, 1.0, 1.5, 1]
accuracy     0.5303571428571429
specificity  0.5242458521870287
sensitivity  0.615
auc          0.5696229260935144
173
[0.1, 1, 200, 2, 0.5, 1.0, 1.5, 2]
accuracy     0.2857142857142857
specificity  0.24091251885369

[0.1, 1, 300, 2, 0, 0.5, 1.5, 3]
accuracy     0.2392857142857143
specificity  0.1888763197586727
sensitivity  0.88
auc          0.5344381598793364
223
[0.1, 1, 300, 2, 0, 0.5, 1.5, 4]
accuracy     0.20892857142857144
specificity  0.15614630467571644
sensitivity  0.88
auc          0.5180731523378582
224
[0.1, 1, 300, 2, 0, 0.5, 2, 1]
accuracy     0.5232142857142857
specificity  0.5147058823529412
sensitivity  0.64
auc          0.5773529411764706
225
[0.1, 1, 300, 2, 0, 0.5, 2, 2]
accuracy     0.3
specificity  0.25825791855203617
sensitivity  0.835
auc          0.5466289592760181
226
[0.1, 1, 300, 2, 0, 0.5, 2, 3]
accuracy     0.2357142857142857
specificity  0.18503016591251886
sensitivity  0.88
auc          0.5325150829562594
227
[0.1, 1, 300, 2, 0, 0.5, 2, 4]
accuracy     0.2
specificity  0.14457013574660635
sensitivity  0.905
auc          0.5247850678733031
228
[0.1, 1, 300, 2, 0, 0.75, 1, 1]
accuracy     0.5214285714285715
specificity  0.5147058823529412
sensitivity  0.615
auc       

...

[0.4, 4, 200, 2, 1, 1.0, 1, 4]
accuracy     0.32321428571428573
specificity  0.28514328808446454
sensitivity  0.81
auc          0.5475716440422322
6688
[0.4, 4, 200, 2, 1, 1.0, 1.5, 1]
accuracy     0.5392857142857143
specificity  0.5300150829562594
sensitivity  0.66
auc          0.5950075414781297
6689
[0.4, 4, 200, 2, 1, 1.0, 1.5, 2]
accuracy     0.375
specificity  0.34121417797888387
sensitivity  0.81
auc          0.5756070889894419
6690
[0.4, 4, 200, 2, 1, 1.0, 1.5, 3]
accuracy     0.3375
specificity  0.29868024132730014
sensitivity  0.835
auc          0.5668401206636501
6691
[0.4, 4, 200, 2, 1, 1.0, 1.5, 4]
accuracy     0.30178571428571427
specificity  0.25822021116138766
sensitivity  0.855
auc          0.5566101055806938
6692
[0.4, 4, 200, 2, 1, 1.0, 2, 1]
accuracy     0.5410714285714285
specificity  0.5340120663650075
sensitivity  0.635
auc          0.5845060331825038
6693
[0.4, 4, 200, 2, 1, 1.0, 2, 2]
accuracy     0.37857142857142856
specificity  0.34502262443438914
sensitivity

[0.4, 4, 300, 2, 0.5, 0.5, 2, 3]
accuracy     0.3732142857142857
specificity  0.3392533936651584
sensitivity  0.81
auc          0.5746266968325792
6743
[0.4, 4, 300, 2, 0.5, 0.5, 2, 4]
accuracy     0.35892857142857143
specificity  0.31998491704374055
sensitivity  0.86
auc          0.5899924585218703
6744
[0.4, 4, 300, 2, 0.5, 0.75, 1, 1]
accuracy     0.5285714285714286
specificity  0.5185143288084465
sensitivity  0.66
auc          0.5892571644042233
6745
[0.4, 4, 300, 2, 0.5, 0.75, 1, 2]
accuracy     0.4267857142857143
specificity  0.40098039215686276
sensitivity  0.76
auc          0.5804901960784313
6746
[0.4, 4, 300, 2, 0.5, 0.75, 1, 3]
accuracy     0.39285714285714285
specificity  0.36255656108597284
sensitivity  0.785
auc          0.5737782805429864
6747
[0.4, 4, 300, 2, 0.5, 0.75, 1, 4]
accuracy     0.35
specificity  0.31221719457013575
sensitivity  0.835
auc          0.5736085972850679
6748
[0.4, 4, 300, 2, 0.5, 0.75, 1.5, 1]
accuracy     0.5357142857142857
specificity  0.5223981

[0.4, 4, 300, 2, 1, 1.0, 1.5, 2]
accuracy     0.375
specificity  0.34121417797888387
sensitivity  0.81
auc          0.5756070889894419
6798
[0.4, 4, 300, 2, 1, 1.0, 1.5, 3]
accuracy     0.3375
specificity  0.29868024132730014
sensitivity  0.835
auc          0.5668401206636501
6799
[0.4, 4, 300, 2, 1, 1.0, 1.5, 4]
accuracy     0.30178571428571427
specificity  0.25822021116138766
sensitivity  0.855
auc          0.5566101055806938
6800
[0.4, 4, 300, 2, 1, 1.0, 2, 1]
accuracy     0.5410714285714285
specificity  0.5340120663650075
sensitivity  0.635
auc          0.5845060331825038
6801
[0.4, 4, 300, 2, 1, 1.0, 2, 2]
accuracy     0.37857142857142856
specificity  0.34502262443438914
sensitivity  0.81
auc          0.5775113122171945
6802
[0.4, 4, 300, 2, 1, 1.0, 2, 3]
accuracy     0.31607142857142856
specificity  0.27941176470588236
sensitivity  0.785
auc          0.5322058823529412
6803
[0.4, 4, 300, 2, 1, 1.0, 2, 4]
accuracy     0.3
specificity  0.2562971342383107
sensitivity  0.86
auc      

[0.4, 4, 400, 2, 0.5, 0.75, 1, 1]
accuracy     0.5303571428571429
specificity  0.5204374057315234
sensitivity  0.66
auc          0.5902187028657617
6853
[0.4, 4, 400, 2, 0.5, 0.75, 1, 2]
accuracy     0.4267857142857143
specificity  0.40098039215686276
sensitivity  0.76
auc          0.5804901960784313
6854
[0.4, 4, 400, 2, 0.5, 0.75, 1, 3]
accuracy     0.39464285714285713
specificity  0.36447963800904976
sensitivity  0.785
auc          0.5747398190045249
6855
[0.4, 4, 400, 2, 0.5, 0.75, 1, 4]
accuracy     0.34464285714285714
specificity  0.30637254901960786
sensitivity  0.835
auc          0.5706862745098039
6856
[0.4, 4, 400, 2, 0.5, 0.75, 1.5, 1]
accuracy     0.5339285714285714
specificity  0.520475113122172
sensitivity  0.71
auc          0.6152375565610859
6857
[0.4, 4, 400, 2, 0.5, 0.75, 1.5, 2]
accuracy     0.4285714285714286
specificity  0.40305429864253395
sensitivity  0.76
auc          0.5815271493212669
6858
[0.4, 4, 400, 2, 0.5, 0.75, 1.5, 3]
accuracy     0.3839285714285714
spe

[0.4, 4, 400, 2, 1, 1.0, 1.5, 4]
accuracy     0.30178571428571427
specificity  0.25822021116138766
sensitivity  0.855
auc          0.5566101055806938
6908
[0.4, 4, 400, 2, 1, 1.0, 2, 1]
accuracy     0.5410714285714285
specificity  0.5340120663650075
sensitivity  0.635
auc          0.5845060331825038
6909
[0.4, 4, 400, 2, 1, 1.0, 2, 2]
accuracy     0.37857142857142856
specificity  0.34502262443438914
sensitivity  0.81
auc          0.5775113122171945
6910
[0.4, 4, 400, 2, 1, 1.0, 2, 3]
accuracy     0.31607142857142856
specificity  0.27941176470588236
sensitivity  0.785
auc          0.5322058823529412
6911
[0.4, 4, 400, 2, 1, 1.0, 2, 4]
accuracy     0.3
specificity  0.2562971342383107
sensitivity  0.86
auc          0.5581485671191553


In [16]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.4, 3, 100, 2, 1, 0.75, 1.5, 1]
0.5553571428571429
0.5416666666666666
0.735
0.6383333333333334


In [17]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.62:
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.1, 4, 400, 2, 1, 0.5, 1, 1]
accuracy : 0.5321428571428571
spes     : 0.5165912518853695
sens     : 0.735
auc      : 0.6257956259426848
------------------------------------------------
parameters : [0.3, 3, 300, 2, 1, 0.5, 2, 1]
accuracy : 0.5428571428571428
spes     : 0.5301282051282051
sens     : 0.71
auc      : 0.6200641025641026
------------------------------------------------
parameters : [0.4, 2, 100, 2, 0, 0.5, 2, 1]
accuracy : 0.5321428571428571
spes     : 0.516553544494721
sens     : 0.735
auc      : 0.6257767722473605
------------------------------------------------
parameters : [0.4, 2, 100, 2, 0, 0.75, 1, 1]
accuracy : 0.5267857142857143
spes     : 0.5107843137254902
sens     : 0.735
auc      : 0.6228921568627451
------------------------------------------------
parameters : [0.4, 2, 100, 2, 0.5, 0.5, 1.5, 1]
accuracy : 0.5303571428571429
spes     : 0.514630467571644
sens     : 0.735
auc      : 0.624815233785822
------------------------------------------------

## Καλύτερες τιμές για Ratio = 1 με min_child_weight=2:

    parameters : [0.4, 3, 100, 2, 1, 0.75, 1.5, 1]
    accuracy : 0.5553571428571429
    spes     : 0.5416666666666666
    sens     : 0.735
    auc      : 0.6383333333333334